# Caribbean Energy Corridor
-
<strong> Code section 08: Results </strong>

| Output | Format |
|----------|----------|



## Functions and libraries

In [1]:
import pandas as pd
import numpy as np

import geopandas as gpd

import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib.ticker import LinearLocator
from matplotlib.colors import Normalize
from mpl_toolkits.axes_grid1 import make_axes_locatable

from scipy.interpolate import RegularGridInterpolator

from myFuncs import *

In [2]:
def haversine(lat1, lon1, lat2, lon2):
    from math import radians, sqrt, sin, cos, atan2

    R = 6371  # radius of Earth in kilometers
    phi1 = radians(lat1)
    phi2 = radians(lat2)
    delta_phi = radians(lat2 - lat1)
    delta_lambda = radians(lon2 - lon1)
    a = sin(delta_phi/2)**2 + cos(phi1) * cos(phi2) * sin(delta_lambda/2)**2
    c = 2 * atan2(sqrt(a), sqrt(1 - a))
    return R * c

### DP 01

In [3]:
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
# import libraries

import numpy as np
# import pandas as pd


# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
# some functions

# find neighbors in an integer grid (diagonal and orthogonal directions)
def find_neighbors(coords):
    neighbors_dict = {}
    total_coords = len(coords)
    processed_coords = 0  # Track how many coordinates we've worked on

    for coord in coords:
        x, y = coord
        neighbors = [(x+i, y+j) for i in [-1, 0, 1] for j in [-1, 0, 1] if i != 0 or j != 0]
        valid_neighbors = [neighbor for neighbor in neighbors if neighbor in coords]
        neighbors_dict[coord] = valid_neighbors

        processed_coords += 1
        completion_percentage = (processed_coords / total_coords) * 100

        print(f"   Progress: {completion_percentage:.1f}%", end='\r')  

    return neighbors_dict

# find neighbors in an integer grid (only orthogonal directions)
def find_neighbors_orthogonal(coords):
    neighbors_dict = {}
    for coord in coords:
        x, y = coord
        neighbors = [(x+i, y) for i in [-1, 0, 1] if i != 0] + [(x, y+j) for j in [-1, 0, 1] if j != 0]
        valid_neighbors = [neighbor for neighbor in neighbors if neighbor in coords]
        neighbors_dict[coord] = valid_neighbors
    return neighbors_dict

# find direction from point b to point a
def find_direction(a, b):
    xdiff = b[0] - a[0]
    ydiff = b[1] - a[1] 

    if xdiff > 0:
        hm = -1         # if xB > xA it moves left
    elif xdiff == 0:
        hm = 0         # if xB = xA it does not move
    else:
        hm = 1         # if xB < xA it moves right

    if ydiff > 0:
        vm = -1         # if yB > yA it moves down
    elif ydiff == 0:
        vm = 0         # if yB + yA it does not move
    else:
        vm = 1         # if yB < yA it moves up

    return (hm, vm)

# finds closest value in another list
def find_closest_value(target, values):
    closest_index = np.argmin(np.abs(values - target))
    return values[closest_index]

# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
def formGrid(btm_df, px, py, qx, qy, reporting):
    if reporting:
        print('______________Step 1: Form Grid______________')


    # adjust points to btm_df
    if reporting:
        print('Adjusting points to btm_df ...')
    px = find_closest_value(px, btm_df['lon'])
    py = find_closest_value(py, btm_df['lat'])
    qx = find_closest_value(qx, btm_df['lon'])
    qy = find_closest_value(qy, btm_df['lat'])

    # create grid 
    if reporting:
        print('Creating grid ...')
    xmax = max(px, qx)
    xmin = min(px, qx)
    ymax = max(py, qy)
    ymin = min(py, qy)
    data = btm_df.query("`lon` >= @xmin and `lon` <= @xmax and `lat` >= @ymin and `lat` <= @ymax")   

    # define A, B, slope
    if px < qx:
        A = (px, py)
        B = (qx, qy)
    elif px > qx:
        A = (qx, qy)
        B = (px, py)

    if A[1] < B[1]:
        slope = 1
    elif A[1] > B[1]:
        slope = -1
    else:
        slope = 0

    lons = data['lon'].drop_duplicates()
    lats = data['lat'].drop_duplicates()

    M = len(lons) - 1
    N = len(lats) - 1

    # get data
    if reporting:
        print('Creating grid positions ...')
    lats = data['lat'].drop_duplicates()
    lons = data['lon'].drop_duplicates()

    # get grid dimensions
    rows = len(lons)
    cols = len(lats)

    # get number of branches G
    G = 2*rows*cols - cols - rows # (m-1)*n + (n-1)*m

    # # # # # # # # # # # # # # # # # # # # # # #
    # create grid of points
    pos = [(i, j) for j in range(cols) for i in range(rows) ]

    if slope == 1:
        posA = (0,0)
        posB = (M,N)
    elif slope == -1:
        posA = (0,N)
        posB = (M,0)

    if reporting:
        print('   Grid positions created.')
        print(f'   # of lats = {len(lats)}')
        print(f'   # of lons = {len(lons)}')
        print(f'   Point A: {posA} = {A}')
        print(f'   Point B: {posB} = {B}')
        print(f'   Slope: {slope}')

    # find valid neighbors of each point
    if reporting:
        print('Finding neighbors...')

    neighbors = find_neighbors(pos)
    if reporting:
        print('   Neighbors found.')

    # # # # # # # # # # # # # # # # # # # # # # #
    # add position column to data
    if reporting:
        print('Adding position to column data ...')
    data = data.copy()
    data['pos'] = pos

    if reporting:
        print('Positioning done.')

    # # # # # # # # # # # # # # # # # # # # # # #
    OO = pos[0]      # start point
    MN = pos[-1]     # end point

    # determine direction of movement
    hm, vm = find_direction(OO,MN)
    # if reporting:
    #     print(f'   Horizontal movement: {-1*hm}')
    #     print(f'   Vertical movement: {-1*vm}')

    if reporting:
        print('Extracting neighbors...')

    # extract neighbors in direction from A to B
    if reporting:
        print('   Extracting A->B neighbors...')
    neighborsAB = {}
    if hm == -1 and vm == -1:
        for key in neighbors:
            neighborsAB[key] =  [value for value in neighbors[key] if value[0] >= key[0] and value[1] >= key[1]]
    elif hm == -1 and vm == 1:
        for key in neighbors:
            neighborsAB[key] =  [value for value in neighbors[key] if value[0] >= key[0] and value[1] <= key[1]]
    elif hm == 1 and vm == -1:
        for key in neighbors:
            neighborsAB[key] =  [value for value in neighbors[key] if value[0] <= key[0] and value[1] >= key[1]]
    elif hm == -1 and vm == -1:
        for key in neighbors:
            neighborsAB[key] =  [value for value in neighbors[key] if value[0] <= key[0] and value[1] <= key[1]]

    # useful note:
            # notice that the neighborsAB are always arranged vertical, horizontal, diagonal
    if reporting:
        print('   Neighbors from A to B extracted.')

    # extract neighbors in direction from B to A
    if reporting:
        print('   Extracting B->A neighbors...')
    neighborsBA = {}
    if hm == -1 and vm == -1:
        for key in neighbors:
            neighborsBA[key] =  [value for value in neighbors[key] if value[0] <= key[0] and value[1] <= key[1]]
    elif hm == -1 and vm == 1:
        for key in neighbors:
            neighborsBA[key] =  [value for value in neighbors[key] if value[0] <= key[0] and value[1] >= key[1]]
    elif hm == 1 and vm == -1:
        for key in neighbors:
            neighborsBA[key] =  [value for value in neighbors[key] if value[0] >= key[0] and value[1] <= key[1]]
    elif hm == -1 and vm == -1:
        for key in neighbors:
            neighborsBA[key] =  [value for value in neighbors[key] if value[0] >= key[0] and value[1] >= key[1]]

    # useful note:
            # notice that the neighborsBA are always arranged diagonal, horizontal, vertical
    if reporting:
        print('   Neighbors from B to A extracted.')

    # # # # # # # # # # # # # # # # # # # # # # # #
    # get flipped btm data (for case 2)
    if reporting:
        print('Generating horizontally flipped bathymetry map (for case 2)...')
    data['x'] = data['pos'].apply(lambda x: x[0])  # Extract y-component from 'pos'
    data['y'] = data['pos'].apply(lambda x: x[1])  # Extract y-component from 'pos' 
    data['y2'] = max(data['y']) - data['y']

    btm_dict = data.set_index('pos')['btm'].to_dict()
    lon_dict = data.set_index('pos')['lon'].to_dict()
    lat_dict = data.set_index('pos')['lat'].to_dict()

    data['lon2'] = data.apply(lambda row: lon_dict[(row['x'], row['y2'])], axis=1)
    data['lat2'] = data.apply(lambda row: lat_dict[(row['x'], row['y2'])], axis=1)
    data['btm2'] = data.apply(lambda row: btm_dict[(row['x'], row['y2'])], axis=1)

    if reporting:
        print('***Grid forming done***')
        print('')

    return data, lons, lats, M, N, A, B, slope, pos, neighbors, neighborsAB, neighborsBA

### DP 02

In [4]:
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
# import libraries

import numpy as np
import pandas as pd
from math import radians, sqrt, sin, cos, atan2

# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
# some functions

# calculate distnace over the surface of the earth using haversine
def haversine(lat1, lon1, lat2, lon2):
    # R = 6371  # radius of Earth in kilometers
    # phi1 = radians(lat1)
    # phi2 = radians(lat2)
    # delta_phi = radians(lat2 - lat1)
    # delta_lambda = radians(lon2 - lon1)
    # a = sin(delta_phi/2)**2 + cos(phi1) * cos(phi2) * sin(delta_lambda/2)**2
    # c = 2 * atan2(sqrt(a), sqrt(1 - a))
    # return R * c
    
    return np.sqrt((lat2-lat1)**2 + (lon2-lon1)**2)

# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
def evaluatePoints(data, neighbors, slope, reporting, prec):
    if reporting:
        print('__________Step 2: Evaluate Points___________')


    # calculate distances between points, considering elevation
    if reporting:
        print('Calculating distances between points, considering elevation ...')

    total_items = len(neighbors)
    index = 0
    distances = []
    for key in neighbors:
        value = neighbors[key]
        n = len(value)

        index += 1
        percentage = (index / total_items) * 100
        print(f"   Progress: {percentage:.1f}%", end='\r') 

        i = key[0]
        j = key[1]

        for p in value:
            ii = p[0]
            jj = p[1]

            a = (i,j)
            b = (ii,jj)

            aidx = data.loc[data['pos'] == a].index[0]
            bidx = data.loc[data['pos'] == b].index[0]

            if slope == 1:
                alat = data['lat'][aidx]
                alon = data['lon'][aidx]

                blat = data['lat'][bidx]
                blon = data['lon'][bidx]

                abtm = data['btm'][aidx]
                bbtm = data['btm'][bidx]
                
            elif slope == -1:
                alat = data['lat2'][aidx]
                alon = data['lon2'][aidx]

                blat = data['lat2'][bidx]
                blon = data['lon2'][bidx]

                abtm = data['btm2'][aidx]
                bbtm = data['btm2'][bidx]

            # calculate haversine distance
            d = haversine(alat,alon,blat,blon)

            # calculate difference in elevation
            h = bbtm - abtm

            # use pythagoras to approximate total distance
            c = round(sqrt(d**2 + h**2),prec)
            
            distances.append({'Start': a, 'End': b, 'Distance': c})

    if reporting:
        print('Creating DataFrame of distances...')
    distances = pd.DataFrame(distances)

    if reporting:
        print('***Points evaluation done***')
        print('')

    return distances


### DP 03

In [5]:
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
# import libraries

import numpy as np
import pandas as pd
from math import radians, sqrt, sin, cos, atan2


# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
# some functions

# find direction from point b to point a
def find_direction(a, b):
    xdiff = b[0] - a[0]
    ydiff = b[1] - a[1] 

    if xdiff > 0:
        hm = -1         # if xB > xA it moves left
    elif xdiff == 0:
        hm = 0         # if xB = xA it does not move
    else:
        hm = 1         # if xB < xA it moves right

    if ydiff > 0:
        vm = -1         # if yB > yA it moves down
    elif ydiff == 0:
        vm = 0         # if yB + yA it does not move
    else:
        vm = 1         # if yB < yA it moves up

    return (hm, vm)

# calculate distnace over the surface of the earth using haversine
def haversine(lat1, lon1, lat2, lon2):
    # R = 6371  # radius of Earth in kilometers
    # phi1 = radians(lat1)
    # phi2 = radians(lat2)
    # delta_phi = radians(lat2 - lat1)
    # delta_lambda = radians(lon2 - lon1)
    # a = sin(delta_phi/2)**2 + cos(phi1) * cos(phi2) * sin(delta_lambda/2)**2
    # c = 2 * atan2(sqrt(a), sqrt(1 - a))
    # return R * c

    return np.sqrt((lat2-lat1)**2 + (lon2-lon1)**2)

# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
def constructSequence(data, neighborsAB, slope, M, N, distances, reporting, prec, lons, lats, save, name):
    if reporting:
        print('_________Step 3: Construct Sequence__________')

    # bathymetry at end points
    if reporting:
        print('Calculating bathymetry at endpoints ...')
    if slope == 1:
        btmA =  data[data['pos'] == (0,0)]['btm'].values[0]
        btmB =  data[data['pos'] == (M,N)]['btm'].values[0]

    elif slope == -1:
        btmA =  data[data['pos'] == (0,0)]['btm2'].values[0]
        btmB =  data[data['pos'] == (M,N)]['btm2'].values[0]

    # # # # # # # # # # # # # # # # # # # # # # #
    # construct value function
    if reporting:
        print('Constructing value function ...')
    V = {}
    U = {}

    total_keys = len(neighborsAB.keys())
    processed = 0
    for key in reversed(list(neighborsAB.keys())):
        value = neighborsAB[key]
        n = len(value)

        processed += 1
        percentage = (processed / total_keys) * 100
        print(f"  Progress: {percentage:.1f}%", end='\r')  

        z = key
        if n == 0:
            # add length to surface at endpoint B
            V[z] = abs(btmB)

            U[z] = (0,0)

        elif n == 1:
            zn = value[0]

            znidx = distances.loc[(distances['End'] == zn) & (distances['Start'] == z)].index[0]

            wn = distances['Distance'][znidx]
            V[z] = abs(wn + V[zn])

            Uh, Uv = find_direction(zn,z)
            U[z] = (Uh, Uv)       

        elif n == 3:
            zv = value[0]
            zh = value[1]
            zd = value[2]
            
            zhidx =  distances.loc[(distances['End'] == zh) & (distances['Start'] == z)].index[0]
            zvidx =  distances.loc[(distances['End'] == zv) & (distances['Start'] == z)].index[0]
            zdidx =  distances.loc[(distances['End'] == zd) & (distances['Start'] == z)].index[0]
            
            wh = distances['Distance'][zhidx]
            wv = distances['Distance'][zvidx]
            wd = distances['Distance'][zdidx]
            
            V[z] = min(abs(wh + V[zh]), abs(wv + V[zv]), abs(wd + V[zd]))

            if V[z] == wh + V[zh]:
                zn = zh
            elif V[z] == wv + V[zv]:
                zn = zv
            elif V[z] == wd + V[zd]:
                zn = zd

            Uh, Uv = find_direction(zn,z)
            U[z] = (Uh, Uv) 

    # add length to surface at endpoint A
    V[(0,0)] = V[(0,0)] + abs(btmA)

    # calculate minimal route
    Vmin = round(V[(0,0)], prec)

    # # # # # # # # # # # # # # # # # # # # # # #
    # recover optimal control sequence
    if reporting:
        print('Recovering optimal control sequence ...')
        
    z = (0,0)
    u = [z]
    while True:

        value = neighborsAB[z]
        n = len(value)

        if n == 0:
            break

        elif n == 1:

            zn = value[0] 

            u.append(zn)

            z = zn

        elif n == 3:
            zv = value[0]
            zh = value[1]
            zd = value[2]
            
            zhidx =  distances.loc[(distances['End'] == zh) & (distances['Start'] == z)].index[0]
            zvidx =  distances.loc[(distances['End'] == zv) & (distances['Start'] == z)].index[0]
            zdidx =  distances.loc[(distances['End'] == zd) & (distances['Start'] == z)].index[0]

            if z == (0,0):
                c = V[z] - abs(btmA)
            else:
                c = V[z]

            ch = V[zh]
            cv = V[zv]
            cd = V[zd]

            if round(c - ch,prec) == distances['Distance'][zhidx]:
                zn = zh
                u.append(zn)
                z = zn
            elif round(c - cv,prec) == distances['Distance'][zvidx]:
                zn = zv
                u.append(zn)
                z = zn
            elif round(c - cd,prec) == distances['Distance'][zdidx]:
                zn = zd
                u.append(zn)
                z = zn

    # # # # # # # # # # # # # # # # # # # # # # #
    # calculate optimal path cost
    pcost = []
    for p in range(len(u)-1):
        start = u[p]
        end = u[p+1]

        pcost.append(distances[(distances['Start'] == start) & (distances['End'] == end)].values[0][2])

    ucost_bottom = sum(pcost)
    ucost = ucost_bottom + abs(btmA) + abs(btmB)

    # flip sequence
    if slope == 1:
        u = u
    elif slope == -1:
        u = [(x, N - y) for x, y in u]

    # calculate area dimensions
    al = haversine(min(lats), min(lons), min(lats), max(lons))
    aw = haversine(min(lats), min(lons), max(lats), min(lons))
    a = al * aw

    # # # # # # # # # # # # # # # # # # # # # # #
    # reporting             
    # check result
    if reporting:
        print('==========================')
        print('Report')
        print(f'Region of analysis: \n Longitude = [{min(lons):.4f},{max(lons):.4f}] °W \n Latitude = [{min(lats):.4f},{max(lats):.4f}] °N \n Length = {al:.0f}(m) \n Width = {aw:.0f} (m) \n Total area ~ {a:.0f} (m^2)')
        if ucost == Vmin:
            print(f'The control sequence finds the least costly path with with a value of {ucost:.2f} m')
            print(f'The optimal control sequence is {u}')
        else:
            print(f'The control sequence does not find the least costly path. \n Dynamic programming  = {Vmin} m \n Control sequence = {ucost} m')

    if reporting:
        print('***Sequence construction done***')
        print('')

    # # # # # # # # # # # # # # # # # # # # # # #
    # extract sequence
    seq = pd.DataFrame()
    for coord in u:
        seqx = data[data['pos'] == coord][['lon', 'lat', 'pos', 'btm']]
        seq = pd.concat([seq,seqx])

    # # # # # # # # # # # # # # # # # # # # # # #
    # save results
    if save:
        # save sequence
        data_name = name + '_data.feather'
        seq_name = name + '_seq.feather'

        # save feather file
        data.to_feather(data_name)
        seq.to_feather(seq_name)     

    return btmA, btmB, u, ucost, data, seq


### DP 04

In [6]:
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
# import libraries

import matplotlib.pyplot as plt
from scipy.interpolate import griddata

import numpy as np
import pandas as pd


# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
# some functions

# 

# # # # # # # # # # # # # # # # # # # # # # # # # # # # # #
def plotRoute(data, reporting, seq, ucost, M, N, btmA, btmB, suptitle, save, name, plot2D, plot3D, levels, msize):
    if reporting:
        if plot2D | plot3D:
            print('_____________Step 4: Plot Route______________')
        else:
            print('No plotting requested.')

    # # # # # # # # # # # # # # # # # # # # # # #
    # plot results
    if plot2D | plot3D:
        btm_2Dcolor = 'twilight_shifted'
        btm_3Dcolor = 'bone'

        x = data['x']
        y = data['y']
        z = data['btm']      
        lon = data['lon']
        lat = data['lat']

        btm_mn = min(z)
        btm_mx = max(z)
        btm_avg = 0.5*(btm_mn+btm_mx)
        btm0_mn = btm_avg
        btm0_mx = -btm_avg

        ulon = seq['lon'].to_list()
        ulat = seq['lat'].to_list()
        upos = [(int(arr[0]), int(arr[1])) for arr in seq['pos'].to_list()]
        ux, uy = zip(*upos)
        uz = [data[(data['x'] == ux) & (data['y'] == uy)]['btm'].values[0] for ux, uy in upos]

        # define grid.
        lons = np.linspace(lon.min(), lon.max(), len(lon.unique()))
        lats = np.linspace(lat.min(), lat.max(), len(lat.unique()))
        lons, lats = np.meshgrid(lons, lats)

    if plot2D:
        if reporting:
            print('Plotting 2D ....')

        fig = plt.figure(figsize=(10, 7))
        ax = plt.axes()    

        # plot optimal path
        plt.plot(ulon,ulat, 'red')

        # Interpolate unstructured D-dimensional data.
        grid = griddata((lon, lat), z, (lons, lats), method='cubic', )

        # Create contour plot.
        plt.contourf(lons, lats, grid, cmap = btm_2Dcolor, norm=plt.Normalize(vmin=btm0_mn, vmax=btm0_mx), levels = levels)
        plt.colorbar(label='Bathymetry (m)')


        # plot labels
        plt.xlabel('Longitue (°W)')
        plt.ylabel('Latitude (°N)')
        plt.title(f'Total distance: {ucost:.0f} m')
        plt.suptitle(suptitle)

        fig1 = plt.gcf()       

        plt.show()

    if plot3D:
        if reporting:
            print('Plotting 3D ....')

        # initialize plot
        fig = plt.figure(figsize=(10, 7))
        ax = plt.axes(projection="3d")

        # scatter plot
        scat = ax.scatter3D(x, y, z, c=z, cmap=btm_3Dcolor,marker='s',alpha = 0.2, norm=plt.Normalize(btm_mn, btm_mx*8), s=msize)

        # colorbar
        cbar = plt.colorbar(scat, shrink=0.5)
        cbar.set_label('Bathymetry (m)')

        # path plot
        ax.plot(ux, uy, uz, color='r', linewidth = 2)
        ax.plot([ux[0],ux[0]], [uy[0],uy[0]], [0, btmA], color='r', linewidth = 2)
        ax.plot([ux[-1],ux[-1]], [uy[-1],uy[-1]], [0, btmB], color='r', linewidth = 2)      
        
        # plot labels
        plt.xlabel('Longitue (°W)')
        plt.ylabel('Latitude (°N)')
        plt.title(f'Total distance: {ucost:.0f} m')
        plt.suptitle(suptitle)

        # set ticks
        nticks = 3
        xticks = np.linspace(min(x), max(x), nticks)
        yticks = np.linspace(min(y), max(y), nticks)

        ax.set_xticks(xticks)
        ax.set_xticklabels(np.round(np.linspace(min(lon),max(lon),nticks),5))
        ax.xaxis.set_tick_params(pad=10)
        ax.xaxis.labelpad = 15

        ax.set_yticks(yticks)
        ax.set_yticklabels(np.round(np.linspace(min(lat),max(lat),nticks),5)) 
        ax.yaxis.set_tick_params(pad=10)
        ax.yaxis.labelpad = 15

        # viewwing angle
        # first angle is rotation along a horizontal axis
        # second angle is rotation along a vertical axis
        # ax.view_init(80, 280)
        ax.view_init(20, 140)

        fig2 = plt.gcf()         
                
        plt.show()

    # # # # # # # # # # # # # # # # # # # # # # #
    # save results
    if save:
        # save plots
        if reporting:
                print('Saving plots...')
        if plot2D:
            fig1_name = name + '2D.png'
            fig1.savefig(fig1_name, dpi=1000)
            if reporting:
                print('2D plot saved.')
        
        if plot3D:
            fig2_name = name + '3D.png'
            fig2.savefig(fig2_name, dpi=1000)
            if reporting:
                print('3D plot saved.')

        

## Read files

In [7]:
mock_bathymetry = pd.read_csv('mock_bathymetry.csv', header=None)
btm_df = pd.read_feather('btm_df.feather')

In [8]:
cec_df = pd.read_feather('cec_df.feather')

cec_lat_min = cec_df['lat'].min()
cec_lat_max = cec_df['lat'].max()
cec_lon_min = cec_df['lon'].min()
cec_lon_max = cec_df['lon'].max()

cec_df_height = cec_lat_max - cec_lat_min
cec_df_width = cec_lon_max - cec_lon_min
cec_df_rat = abs(cec_df_height/cec_df_width)

cec_height = haversine(cec_lat_min, cec_lon_min, cec_lat_max, cec_lon_min)
cec_width = haversine(cec_lat_min, cec_lon_min, cec_lat_min, cec_lon_max)
cec_area = cec_height * cec_width
# cec_df

regions = pd.read_csv('regions.csv')
regs = regions['region']
reg_names = regions['name']
reg_lat_mins = regions['lat min']
reg_lat_maxs = regions['lat max']
reg_lon_mins = regions['lon min']
reg_lon_maxs = regions['lon max']
reg_colors = regions['color']
# regions

reports = pd.read_csv('reports.csv')
# reports

## Create new DataFrames

In [9]:
shr_df = cec_df[(cec_df['btm'] >= -1) & (cec_df['btm'] <= 0)]
shr_df.to_feather('shr_df.feataher')

## Parameters for plots

In [10]:
# # # fig specs
# fsize = 16
# fsize_sm = fsize - 2
# ftype = 'serif'
# fig_width = 10
# fig_height= 6

# # fig specs
fsize = 24
fsize_sm = fsize - 2
ftype = 'Arial'
fweight = 'bold'
fig_width = 10
fig_height= 6

plt.rcParams['font.size'] = fsize  
plt.rcParams['font.family'] = ftype
plt.rcParams['legend.fontsize'] = fsize
plt.rcParams['axes.titlesize'] = fsize  
plt.rcParams['axes.labelsize'] = fsize    
plt.rcParams['xtick.labelsize'] = fsize   
plt.rcParams['ytick.labelsize'] = fsize 

figpath = r"C:\Users\dagui\OneDrive - purdue.edu\Research - L Castillo\Green Engines\Caribbean Energy Corridor\article\figures\nature" 

# # world map
world = gpd.read_file('C:\\Users\\dagui\\OneDrive - purdue.edu\\Research - L Castillo\\World Maps\\data\\ne_110m_admin_0_countries\\ne_110m_admin_0_countries.shp')

# # cec coordinates
lats = cec_df['lat'].values
lons = cec_df['lon'].values
btms = cec_df['btm'].values
lon_mesh, lat_mesh = np.meshgrid(np.unique(lons), np.unique(lats))

# # labels
month_list = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']

## Bathymetry data

In [11]:
# # # font sizes
# plt.rcParams['font.size'] = fsize  
# plt.rcParams['font.family'] = ftype
# plt.rcParams['legend.fontsize'] = fsize
# plt.rcParams['axes.titlesize'] = fsize  
# plt.rcParams['axes.labelsize'] = fsize    
# plt.rcParams['xtick.labelsize'] = fsize   
# plt.rcParams['ytick.labelsize'] = fsize   

# # # create plot
# fig, ax = plt.subplots(figsize=(fig_width, fig_width*cec_df_rat), dpi=1000, subplot_kw={"projection": "3d"})

# # # create meshgrid 
# btm_nlons = btm_df['lon'].nunique()
# btm_nlats = btm_df['lat'].nunique()
# X = btm_df['lon'].values.reshape(btm_nlats, btm_nlons)
# Y = btm_df['lat'].values.reshape(btm_nlats, btm_nlons)
# Z = btm_df['btm'].values.reshape(btm_nlats, btm_nlons)

# # # plot the surface with terrain colormap
# surf = ax.plot_surface(X, Y, Z, cmap=cm.gist_earth, linewidth=1000, antialiased=True, alpha=0.9)

# # # colorbar
# fig.colorbar(surf, shrink=0.45, aspect=20, pad=0.01, label='Bathymetry (m)')

# # # set aspect ratio
# x_range = np.ptp(X)
# y_range = np.ptp(Y)
# z_range = np.ptp(Z)

# x_aspect = 1.0 
# y_aspect = 1.0
# z_aspect = 90.0 

# box_aspect = (x_aspect / x_range, y_aspect / y_range, z_aspect / z_range)

# ax.set_box_aspect(box_aspect)

# # # set viewing angle
# ax.view_init(elev=25, azim=-75)

# # # set labels and ticks
# ax.set_xlabel('Longitude (°W)', fontsize=fsize, labelpad=15)
# ax.set_ylabel('Latitude (°N)', fontsize=fsize, labelpad=15)
# ax.set_zlabel('', fontsize=fsize)
# ax.set_zticks([])

# # # plot shorelines
# z0 = 0
# ax.scatter(shr_df['lon'], shr_df['lat'], z0 , s=1, c='black')

# # # final touches
# plt.subplots_adjust(left=0, right=1, bottom=0, top=1)
# plt.show()


## Mock bathymetry data

In [12]:
# dpex_data = pd.read_csv('node_costs.csv', header=None)
mock_data = pd.read_csv('mock_bathymetry.csv', header=None)

mock_df = pd.DataFrame(columns=['lon', 'lat', 'btm']) 

for i in range(mock_data.shape[0]):
    for j in range(mock_data.shape[1]):
        new_row = pd.DataFrame({'lon': [j], 'lat': [i], 'btm': [mock_data[j][i]]})  
        mock_df = pd.concat([mock_df, new_row], ignore_index=True) 


# # font sizes
plt.rcParams['font.size'] = fsize  
plt.rcParams['font.family'] = ftype
plt.rcParams['legend.fontsize'] = fsize
plt.rcParams['axes.titlesize'] = fsize  
plt.rcParams['axes.labelsize'] = fsize    
plt.rcParams['xtick.labelsize'] = fsize   
plt.rcParams['ytick.labelsize'] = fsize   

# # create plot
fig, ax = plt.subplots(figsize=(fig_width, fig_width*cec_df_rat), dpi=1000, subplot_kw={"projection": "3d"})

# # # add 0 level
# ax.scatter(mock_df['lon'], mock_df['lat'], 0 , s=1, c='black', alpha=0.15)

# # create meshgrid 
mck_nlons = mock_df['lon'].nunique()
mck_nlats = mock_df['lat'].nunique()
X = mock_df['lon'].values.reshape(mck_nlats, mck_nlons)
Y = mock_df['lat'].values.reshape(mck_nlats, mck_nlons)
Z = mock_df['btm'].values.reshape(mck_nlats, mck_nlons)

X = X.astype(float)  # or X = np.asarray(X, dtype=float)
Y = Y.astype(float)
Z = Z.astype(float)

# # plot the surface with terrain colormap
surf = ax.plot_surface(X, Y, Z, cmap=cm.gist_earth, linewidth=10000, antialiased=True, alpha=0.9, vmax=Z.max()*1.1)

# # # colorbar
# fig.colorbar(surf, shrink=0.45, aspect=20, pad=0.01, label='$z$ values')

# # set aspect ratio
x_range = np.ptp(X)
y_range = np.ptp(Y)
z_range = np.ptp(Z)

x_aspect = 1.0 
y_aspect = 1.0
z_aspect = 7

box_aspect = (x_aspect / x_range, y_aspect / y_range, z_aspect / z_range)

ax.set_box_aspect(box_aspect)

# # set viewing angle
ax.view_init(elev=25, azim=-60)

# # set labels and ticks
ax.set_xlabel('$x$-axis', fontsize=fsize, labelpad=15)
ax.set_ylabel('$y$-axis', fontsize=fsize, labelpad=15)
ax.set_zlabel('', fontsize=fsize)
ax.set_zticks([])
ax.set_zlim([-50, 100])

ax.xaxis.set_pane_color((1.0, 1.0, 1.0, 0.0))
ax.yaxis.set_pane_color((1.0, 1.0, 1.0, 0.0))
ax.zaxis.set_pane_color((1.0, 1.0, 1.0, 0.0))

ax.grid(False)

# # final touches
plt.subplots_adjust(left=0, right=1, bottom=0, top=1)
plt.show()


In [13]:
# # font sizes
plt.rcParams['font.size'] = fsize  
plt.rcParams['font.family'] = ftype
plt.rcParams['legend.fontsize'] = fsize
plt.rcParams['axes.titlesize'] = fsize  
plt.rcParams['axes.labelsize'] = fsize    
plt.rcParams['xtick.labelsize'] = fsize   
plt.rcParams['ytick.labelsize'] = fsize   

# # create figure
fig, ax = plt.subplots(figsize=(fig_width, fig_width*cec_df_rat), dpi=1000)

divider = make_axes_locatable(ax)
cbar_height_ratio = 0.25

norm = Normalize(vmin=mock_df['btm'].min(), vmax=mock_df['btm'].max()*1.1)
scatter = ax.scatter(mock_df['lon'], mock_df['lat'], c=mock_df['btm'], cmap='gist_earth', s=100, norm=norm, marker='s')


# Create axes for the colorbar using make_axes_locatable
cax = divider.append_axes("right", size="5%", pad=1.1)  # Re-use the divider to avoid creating a new one.
cbar= plt.colorbar(scatter, cax=cax, label='$z$ values')

# Make the colorbar the same height as the plot and position it at the bottom
pos = cax.get_position()
pos.y1 = pos.y0 + cbar_height_ratio * (pos.y1 - pos.y0)  # Adjust the top of the second colorbar
cax.set_position(pos)

# # set labels and ticks
ax.set_xlabel('$x$-axis', fontsize=fsize, labelpad=15)
ax.set_ylabel('$y$-axis', fontsize=fsize, labelpad=15)

plt.show()

In [14]:
# # 
px = mock_df['lon'].tolist()[0]
py = mock_df['lon'].tolist()[0]
qx = mock_df['lon'].tolist()[-1]
qy = mock_df['lat'].tolist()[-1]

reporting = True
prec = 6
save = False
name = 'mock_btm'

data, lons, lats, M, N, A, B, slope, pos, neighbors, neighborsAB, neighborsBA  = formGrid(mock_df, px, py, qx, qy, reporting)
distances = evaluatePoints(data, neighbors, slope, reporting, prec)
btmA, btmB, u, ucost, data, seq = constructSequence(data, neighborsAB, slope, M, N, distances, reporting, prec, lons, lats, save, name)


______________Step 1: Form Grid______________
Adjusting points to btm_df ...
Creating grid ...
Creating grid positions ...
   Grid positions created.
   # of lats = 24
   # of lons = 22
   Point A: (0, 0) = (0, 0)
   Point B: (21, 23) = (21, 23)
   Slope: 1
Finding neighbors...
   Neighbors found.
Adding position to column data ...
Positioning done.
Extracting neighbors...
   Extracting A->B neighbors...
   Neighbors from A to B extracted.
   Extracting B->A neighbors...
   Neighbors from B to A extracted.
Generating horizontally flipped bathymetry map (for case 2)...
***Grid forming done***

__________Step 2: Evaluate Points___________
Calculating distances between points, considering elevation ...
Creating DataFrame of distances...
***Points evaluation done***

_________Step 3: Construct Sequence__________
Calculating bathymetry at endpoints ...
Constructing value function ...
Recovering optimal control sequence ...
Report
Region of analysis: 
 Longitude = [0.0000,21.0000] °W 
 Latit

In [15]:
# seqDF = seq
# suptitle = ''
# plot2D = False
# plot3D = True

# plotRoute(data, reporting, seqDF, ucost, M, N, btmA, btmB, suptitle, save, name, plot2D, plot3D, 25, 10)

In [16]:
# # # post processing of seq

# # Extract x and y coordinates from 'pos' column
# seq['pos'] = seq['pos'].astype(str).str.replace(r'[()]', '', regex=True)  # Remove parentheses
# seq[['x', 'y']] = seq['pos'].str.split(', ', expand=True)
# seq['x'] = pd.to_numeric(seq['x'])
# seq['y'] = pd.to_numeric(seq['y'])


In [17]:
# dpex_data = pd.read_csv('node_costs.csv', header=None)
mock_data = pd.read_csv('mock_bathymetry.csv', header=None)

mock_df = pd.DataFrame(columns=['lon', 'lat', 'btm']) 

for i in range(mock_data.shape[0]):
    for j in range(mock_data.shape[1]):
        new_row = pd.DataFrame({'lon': [j], 'lat': [i], 'btm': [mock_data[j][i]]})  
        mock_df = pd.concat([mock_df, new_row], ignore_index=True) 


# # font sizes
plt.rcParams['font.size'] = fsize  
plt.rcParams['font.family'] = ftype
plt.rcParams['legend.fontsize'] = fsize
plt.rcParams['axes.titlesize'] = fsize  
plt.rcParams['axes.labelsize'] = fsize    
plt.rcParams['xtick.labelsize'] = fsize   
plt.rcParams['ytick.labelsize'] = fsize   

# # create plot
fig, ax = plt.subplots(figsize=(fig_width, fig_width*cec_df_rat), dpi=1000, subplot_kw={"projection": "3d"})

# # # add 0 level
# ax.scatter(mock_df['lon'], mock_df['lat'], 0 , s=1, c='black', alpha=0.15)

# # create meshgrid 
mck_nlons = mock_df['lon'].nunique()
mck_nlats = mock_df['lat'].nunique()
X = mock_df['lon'].values.reshape(mck_nlats, mck_nlons)
Y = mock_df['lat'].values.reshape(mck_nlats, mck_nlons)
Z = mock_df['btm'].values.reshape(mck_nlats, mck_nlons)

X = X.astype(float)  # or X = np.asarray(X, dtype=float)
Y = Y.astype(float)
Z = Z.astype(float)

# # plot the surface with terrain colormap
surf = ax.plot_surface(X, Y, Z, cmap=cm.gist_earth, linewidth=10000, antialiased=True, alpha=0.6, vmax=Z.max()*1.1)

# # # colorbar
# fig.colorbar(surf, shrink=0.45, aspect=20, pad=0.01, label='$z$ values')

# # plot sequence
ax.plot(seq['lon'], seq['lat'], seq['btm'], color='red', linewidth=5)
# ax.scatter(seq['x'], seq['y'], color='red', s=10)

# # set aspect ratio
x_range = np.ptp(X)
y_range = np.ptp(Y)
z_range = np.ptp(Z)

x_aspect = 1.0 
y_aspect = 1.0
z_aspect = 7

box_aspect = (x_aspect / x_range, y_aspect / y_range, z_aspect / z_range)

ax.set_box_aspect(box_aspect)

# # set viewing angle
ax.view_init(elev=25, azim=-60)

# # set labels and ticks
ax.set_xlabel('$x$-axis', fontsize=fsize, labelpad=15)
ax.set_ylabel('$y$-axis', fontsize=fsize, labelpad=15)
ax.set_zlabel('', fontsize=fsize)
ax.set_zticks([])

ax.grid(False)

# # final touches
plt.subplots_adjust(left=0, right=1, bottom=0, top=1)
plt.show()


In [18]:
# # font sizes
plt.rcParams['font.size'] = fsize  
plt.rcParams['font.family'] = ftype
plt.rcParams['legend.fontsize'] = fsize
plt.rcParams['axes.titlesize'] = fsize  
plt.rcParams['axes.labelsize'] = fsize    
plt.rcParams['xtick.labelsize'] = fsize   
plt.rcParams['ytick.labelsize'] = fsize   

# # create figure
fig, ax = plt.subplots(figsize=(fig_width, fig_width*cec_df_rat), dpi=1000)

divider = make_axes_locatable(ax)
cbar_height_ratio = 0.25

# # plot terrain
norm = Normalize(vmin=mock_df['btm'].min(), vmax=mock_df['btm'].max()*1.1)
scatter = ax.scatter(mock_df['lon'], mock_df['lat'], c=mock_df['btm'], cmap='gist_earth', s=110, norm=norm, marker='s')

# # plot sequence
ax.plot(seq['lon'], seq['lat'], color='red', linewidth=10)

# Create axes for the colorbar using make_axes_locatable
cax = divider.append_axes("right", size="5%", pad=1.1)  # Re-use the divider to avoid creating a new one.
cbar= plt.colorbar(scatter, cax=cax, label='$z$ values')

# Make the colorbar the same height as the plot and position it at the bottom
pos = cax.get_position()
pos.y1 = pos.y0 + cbar_height_ratio * (pos.y1 - pos.y0)  # Adjust the top of the second colorbar
cax.set_position(pos)

# # set labels and ticks
ax.set_xlabel('$x$-axis', fontsize=fsize, labelpad=15)
ax.set_ylabel('$y$-axis', fontsize=fsize, labelpad=15)

plt.show()

## DP example

In [19]:
# # dpex_data = pd.read_csv('node_costs.csv', header=None)
# dpex_data = pd.read_csv('mock_bathymetry.csv', header=None)

# dpex_df = pd.DataFrame(columns=['lon', 'lat', 'btm']) 

# for i in range(dpex_data.shape[0]):
#     for j in range(dpex_data.shape[1]):
#         new_row = pd.DataFrame({'lon': [j], 'lat': [i], 'btm': [dpex_data[j][i]]})  
#         dpex_df = pd.concat([dpex_df, new_row], ignore_index=True) 

In [20]:
# fig, ax = plt.subplots(figsize=(fig_width*0.75, fig_width*cec_df_rat*0.75), dpi=1000)

# ax.scatter(dpex_df['lon'], dpex_df['lat'])
# ax.scatter(0,0, marker="D", color='green', s=100, label='$x_A$')
# ax.scatter(max(dpex_df['lon']), max(dpex_df['lat']), marker="*", color='red', s=175, label='$x_B$')

# for i, row in dpex_df.iterrows():
#     # Annotate each point with the corresponding value of `btm`
#     ax.annotate(row['btm'], (row['lon'], row['lat']), textcoords="offset points", xytext=(5,0), ha='left')

# ax.set_xlim([min(dpex_df['lon'])-0.5, max(dpex_df['lon'])+0.5])
# ax.set_ylim([min(dpex_df['lat'])-0.5, max(dpex_df['lat'])+0.5])

# ax.set_xticks([])
# ax.set_yticks([])

# ax.annotate('', xy=(1.05, 0), xycoords='axes fraction', xytext=(0, 0), 
#             arrowprops=dict(arrowstyle="->", color='black'))
# ax.annotate('', xy=(0, 1.05), xycoords='axes fraction', xytext=(0, 0), 
#             arrowprops=dict(arrowstyle="->", color='black'))

# ax.set_xlabel('$x_1$-axis')
# ax.set_ylabel('$x_2$-axis')

# ax.spines['top'].set_visible(False)
# ax.spines['right'].set_visible(False)
# # ax.spines['bottom'].set_visible(False)
# # ax.spines['left'].set_visible(False)

# legend = plt.legend(loc='upper center', bbox_to_anchor=(0.5, 1.15), ncol=2, frameon=False)

# plt.show()

In [21]:
# px = dpex_df['lon'].tolist()[0]
# py = dpex_df['lon'].tolist()[0]
# qx = dpex_df['lon'].tolist()[-1]
# qy = dpex_df['lat'].tolist()[-1]

# reporting = True
# prec = 6
# save = False
# name = 'dpex'

# data, lons, lats, M, N, A, B, slope, pos, neighbors, neighborsAB, neighborsBA  = formGrid(dpex_df, px, py, qx, qy, reporting)
# distances = evaluatePoints(data, neighbors, slope, reporting, prec)
# btmA, btmB, u, ucost, data, seq = constructSequence(data, neighborsAB, slope, M, N, distances, reporting, prec, lons, lats, save, name)


In [22]:
# fig, ax = plt.subplots(figsize=(fig_width*0.75, fig_width*cec_df_rat*0.75), dpi=1000)

# ax.scatter(dpex_df['lon'], dpex_df['lat'])
# ax.scatter(0,0, marker="D", color='green', s=100, label='$x_A$')
# ax.scatter(max(dpex_df['lon']), max(dpex_df['lat']), marker="*", color='red', s=175, label='$x_B$')

# for i, row in dpex_df.iterrows():
#     # Annotate each point with the corresponding value of `btm`
#     ax.annotate(row['btm'], (row['lon'], row['lat']), textcoords="offset points", xytext=(5,0), ha='left')

# ax.plot(seq['lon'], seq['lat'], c='purple', label='Optimal route')

# ax.set_xlim([min(dpex_df['lon'])-0.5, max(dpex_df['lon'])+0.5])
# ax.set_ylim([min(dpex_df['lat'])-0.5, max(dpex_df['lat'])+0.5])

# ax.set_xticks([])
# ax.set_yticks([])

# ax.annotate('', xy=(1.05, 0), xycoords='axes fraction', xytext=(0, 0), 
#             arrowprops=dict(arrowstyle="->", color='black'))
# ax.annotate('', xy=(0, 1.05), xycoords='axes fraction', xytext=(0, 0), 
#             arrowprops=dict(arrowstyle="->", color='black'))

# ax.set_xlabel('$x_1$-axis')
# ax.set_ylabel('$x_2$-axis')


# ax.spines['top'].set_visible(False)
# ax.spines['right'].set_visible(False)
# # ax.spines['bottom'].set_visible(False)
# # ax.spines['left'].set_visible(False)

# legend = plt.legend(loc='upper center', bbox_to_anchor=(0.5, 1.15), ncol=3, frameon=False)

# plt.show()